In [1]:
from dash import Dash, html, dcc, Input, Output, callback
import pandas as pd
import plotly.express as px
import datetime as dt

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = Dash(__name__, external_stylesheets=external_stylesheets)

df = pd.read_csv('smart-meadow.csv')
df["date"] = pd.to_datetime(df["TIMESTAMP"])
months = df["date"].dt.strftime("%m/%y").unique().tolist()


/var/folders/hf/ljtgk4gj2cdgq955jzdyfxjw0000gp/T/ipykernel_15914/488082001.py:11: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.



In [2]:
df

TIMESTAMP  RECORD  PTemp_C_Avg  AirTF_Avg     RH  Rain_mm_Tot  \
0       4/12/24 10:29       0        19.96      62.10  49.02          0.0   
1       4/12/24 10:29       1        19.96      62.10  49.01          0.0   
2       4/12/24 10:29       2        19.96      62.12  49.02          0.0   
3       4/12/24 10:29       3        19.97      62.15  49.03          0.0   
4       4/12/24 10:29       4        19.97      62.17  48.99          0.0   
...               ...     ...          ...        ...    ...          ...   
225323   7/2/24 13:26  700907        38.96      94.70  50.80          0.0   
225324   7/2/24 13:27  700908        38.97      94.70  50.93          0.0   
225325   7/2/24 13:27  700909        38.99      94.70  50.84          0.0   
225326   7/2/24 13:27  700910        39.00      94.70  50.81          0.0   
225327   7/2/24 13:27  700911        39.01      94.70  50.80          0.0   

        WS_mph  VWC_Avg  EC_Avg  T_Avg                date  
0        0.000    0.407   0.257  68.49 2024-04-12 10:29:00  
1        0.000    0.407   0.257  68.50 2024-04-12 10:29:00  
2        5.096    0.407   0.257  68.56 2024-04-12 10:29:00  
3        4.760    0.407   0.257  68.63 2024-04-12 10:29:00  
4        4.089    0.407   0.257  68.63 2024-04-12 10:29:00  
...        ...      ...     ...    ...                 ...  
225323   3.083    0.216   0.091  90.60 2024-07-02 13:26:00  
225324   1.071    0.216   0.091  90.60 2024-07-02 13:27:00  
225325   0.735    0.216   0.091  90.60 2024-07-02 13:27:00  
225326   2.077    0.216   0.091  90.60 2024-07-02 13:27:00  
225327   0.000    0.216   0.091  90.60 2024-07-02 13:27:00  

[225328 rows x 11 columns]

In [43]:
df['date']

0        2024-04-12 10:29:00
1        2024-04-12 10:29:00
2        2024-04-12 10:29:00
3        2024-04-12 10:29:00
4        2024-04-12 10:29:00
                 ...        
225323   2024-07-02 13:26:00
225324   2024-07-02 13:27:00
225325   2024-07-02 13:27:00
225326   2024-07-02 13:27:00
225327   2024-07-02 13:27:00
Name: date, Length: 225328, dtype: datetime64[ns]

In [44]:
px.line(df,  x='RECORD', y="RH")


In [4]:

app.layout = [
    html.H1(children='Meadow Viewer', style={'textAlign':'center'}),
    dcc.Dropdown(df.columns[3:10], 'RH', id='dropdown-selection'),
    dcc.Graph(id='graph-content')
]

@callback(
    Output('graph-content', 'figure'),
    Input('dropdown-selection', 'value')
)
def update_graph(value):
    # dff = df[value]
    print(value)
    return px.line(df, x='RECORD', y="RH")

if __name__ == '__main__':
    app.run(debug=True)

AssertionError: The setup method 'errorhandler' can no longer be called on the application. It has already handled its first request, any changes will not be applied consistently.
Make sure all imports, decorators, functions, etc. needed to set up the application are done before running it.

In [22]:
from dash import Dash, html, dcc, Input, Output, callback
import pandas as pd
import plotly.express as px

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = Dash(__name__, external_stylesheets=external_stylesheets)

df = pd.read_csv('https://plotly.github.io/datasets/country_indicators.csv')


app.layout = html.Div([
    html.Div([

        html.Div([
            dcc.Dropdown(
                df['Indicator Name'].unique(),
                'Fertility rate, total (births per woman)',
                id='crossfilter-xaxis-column',
            ),
            dcc.RadioItems(
                ['Linear', 'Log'],
                'Linear',
                id='crossfilter-xaxis-type',
                labelStyle={'display': 'inline-block', 'marginTop': '5px'}
            )
        ],
        style={'width': '49%', 'display': 'inline-block'}),

        html.Div([
            dcc.Dropdown(
                df['Indicator Name'].unique(),
                'Life expectancy at birth, total (years)',
                id='crossfilter-yaxis-column'
            ),
            dcc.RadioItems(
                ['Linear', 'Log'],
                'Linear',
                id='crossfilter-yaxis-type',
                labelStyle={'display': 'inline-block', 'marginTop': '5px'}
            )
        ], style={'width': '49%', 'float': 'right', 'display': 'inline-block'})
    ], style={
        'padding': '10px 5px'
    }),

    html.Div([
        dcc.Graph(
            id='crossfilter-indicator-scatter',
            hoverData={'points': [{'customdata': 'Japan'}]}
        )
    ], style={'width': '49%', 'display': 'inline-block', 'padding': '0 20'}),
    html.Div([
        dcc.Graph(id='x-time-series'),
        dcc.Graph(id='y-time-series'),
    ], style={'display': 'inline-block', 'width': '49%'}),

    html.Div(dcc.Slider(
        df['Year'].min(),
        df['Year'].max(),
        step=None,
        id='crossfilter-year--slider',
        value=df['Year'].max(),
        marks={str(year): str(year) for year in df['Year'].unique()}
    ), style={'width': '49%', 'padding': '0px 20px 20px 20px'})
])


@callback(
    Output('crossfilter-indicator-scatter', 'figure'),
    Input('crossfilter-xaxis-column', 'value'),
    Input('crossfilter-yaxis-column', 'value'),
    Input('crossfilter-xaxis-type', 'value'),
    Input('crossfilter-yaxis-type', 'value'),
    Input('crossfilter-year--slider', 'value'))
def update_graph(xaxis_column_name, yaxis_column_name,
                 xaxis_type, yaxis_type,
                 year_value):
    dff = df[df['Year'] == year_value]

    fig = px.scatter(x=dff[dff['Indicator Name'] == xaxis_column_name]['Value'],
            y=dff[dff['Indicator Name'] == yaxis_column_name]['Value'],
            hover_name=dff[dff['Indicator Name'] == yaxis_column_name]['Country Name']
            )

    fig.update_traces(customdata=dff[dff['Indicator Name'] == yaxis_column_name]['Country Name'])

    fig.update_xaxes(title=xaxis_column_name, type='linear' if xaxis_type == 'Linear' else 'log')

    fig.update_yaxes(title=yaxis_column_name, type='linear' if yaxis_type == 'Linear' else 'log')

    fig.update_layout(margin={'l': 40, 'b': 40, 't': 10, 'r': 0}, hovermode='closest')

    return fig


def create_time_series(dff, axis_type, title):

    fig = px.scatter(dff, x='Year', y='Value')

    fig.update_traces(mode='lines+markers')

    fig.update_xaxes(showgrid=False)

    fig.update_yaxes(type='linear' if axis_type == 'Linear' else 'log')

    fig.add_annotation(x=0, y=0.85, xanchor='left', yanchor='bottom',
                       xref='paper', yref='paper', showarrow=False, align='left',
                       text=title)

    fig.update_layout(height=225, margin={'l': 20, 'b': 30, 'r': 10, 't': 10})

    return fig


@callback(
    Output('x-time-series', 'figure'),
    Input('crossfilter-indicator-scatter', 'hoverData'),
    Input('crossfilter-xaxis-column', 'value'),
    Input('crossfilter-xaxis-type', 'value'))
def update_x_timeseries(hoverData, xaxis_column_name, axis_type):
    country_name = hoverData['points'][0]['customdata']
    dff = df[df['Country Name'] == country_name]
    dff = dff[dff['Indicator Name'] == xaxis_column_name]
    title = '<b>{}</b><br>{}'.format(country_name, xaxis_column_name)
    return create_time_series(dff, axis_type, title)


@callback(
    Output('y-time-series', 'figure'),
    Input('crossfilter-indicator-scatter', 'hoverData'),
    Input('crossfilter-yaxis-column', 'value'),
    Input('crossfilter-yaxis-type', 'value'))
def update_y_timeseries(hoverData, yaxis_column_name, axis_type):
    dff = df[df['Country Name'] == hoverData['points'][0]['customdata']]
    dff = dff[dff['Indicator Name'] == yaxis_column_name]
    return create_time_series(dff, axis_type, yaxis_column_name)


if __name__ == '__main__':
    app.run(debug=True)

In [36]:
from dash import Dash, html, dcc, callback, Output, Input
import plotly.express as px
import pandas as pd

df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/gapminder_unfiltered.csv')

app = Dash()

# Requires Dash 2.17.0 or later
app.layout = [
    html.H1(children='Title of Dash App', style={'textAlign':'center'}),
    dcc.Dropdown(df.country.unique(), 'Canada', id='dropdown-selection'),
    dcc.Graph(id='graph-content')
]

@callback(
    Output('graph-content', 'figure'),
    Input('dropdown-selection', 'value')
)
def update_graph(value):
    dff = df[df.country==value]
    return px.line(dff, x='year', y='pop')

if __name__ == '__main__':
    app.run(debug=True)